## Manual processing of a video using the FPGA acceleration

This notebook shows how the Cortex processor can load a video from storage memory and input it frame-by-frame through the FPGA lane detector. The resulting lines are fetched from hardware and put into the out_buffer in host memory by the DMA. Plotting of the lines for visualization purposes is done in software using OpenCV.

In [1]:
from pynq import allocate, Overlay, Clocks
from matplotlib import pyplot as plot
from IPython.display import Video
import numpy as np
import cv2 as cv
import math

# Load the system into the PL
system = Overlay("bd_wrapper.bit");
dma = system.axi_dma_0
vpu = system.vpu_accel_0

# For some reason this clock gets reset to 66 MHz
Clocks.fclk0_mhz = 100

# Check if the VPU IP core is the right component by chekcing if the registers exist
for reg in ["in_width", "in_height", "seg_thres", "g_sigma", "e_thres", "h_thres"]:
    assert(hasattr(vpu.register_map, reg))

vpu.register_map

RegisterMap {
  CTRL = Register(AP_START=0, AP_DONE=0, AP_IDLE=1, AP_READY=0, RESERVED_1=0, AUTO_RESTART=0, RESERVED_2=0, RESERVED_3=0, RESERVED_4=0),
  GIER = Register(Enable=0, RESERVED=0),
  IP_IER = Register(CHAN0_INT_EN=0, CHAN1_INT_EN=0, RESERVED_0=0, CHAN2_INT_EN=0, RESERVED_1=0),
  IP_ISR = Register(CHAN0_INT_ST=0, CHAN1_INT_ST=0, RESERVED_0=0, CHAN2_INT_ST=0, RESERVED_1=0),
  in_height = Register(in_height=write-only),
  in_width = Register(in_width=write-only),
  seg_thres = Register(seg_thres=write-only, RESERVED=write-only),
  g_sigma = Register(g_sigma=write-only),
  e_thres = Register(e_thres=write-only, RESERVED=write-only),
  h_thres = Register(h_thres=write-only, RESERVED=write-only)
}

### Setup video input source and output destination

In [2]:
# Dimensions of the video
max_width = 1280
max_height = 720

# Fixed maximum accumulator spaces (in hardware)
max_lines = 32
# Hough result error margin in radians
theta_margin = 0.05 # ~3 deg, 2x theta res.

# Input
vrd = cv.VideoCapture("night4.m4v")
vrd.set(cv.CAP_PROP_FRAME_WIDTH, max_width)
vrd.set(cv.CAP_PROP_FRAME_HEIGHT, max_height)

# Output, use VP8 in WEBM container for Jupyter embed
out_file_name = "night4_out.webm"
vwc = cv.VideoWriter_fourcc(*"vp80")
vwr = cv.VideoWriter(out_file_name, vwc, 20.0, (max_width,  max_height))

### Configure the shared memory between SW/HW

In [3]:
# Configure the DMA
in_buffer = allocate(shape=(max_height, max_width, 3), dtype=np.uint8, cacheable=1)
out_buffer = allocate(shape=(2, max_lines), dtype=np.int32, cacheable=1)
fl_buffer = allocate(shape=(2, max_lines), dtype=np.float32, cacheable=1)

# Default settings for most scenarios
seg_thres = 70
g_sigma = 2.5
e_thres = 20
h_thres = 150

# Configure the IP core
vpu.register_map.in_width = max_width
vpu.register_map.in_height = max_height
vpu.register_map.seg_thres = seg_thres
vpu.register_map.g_sigma = e_thres
vpu.register_map.e_thres = e_thres
vpu.register_map.h_thres = h_thres

### Run the main loop

In [4]:
# Amount of data points to take into account when averaging
roll_amount = 10
# 90 degrees in radians
deg90_rad = math.pi / 2
# Sensitivity of the angle detection algorithm
angle_sens = 1.75

num_frames = 0
total_ticks = 0
left_rho_roll = 0
left_theta_roll = 0
right_rho_roll = 0
right_theta_roll = 0

# Approximate the rolling average
def roll_avg(avg, new):
    avg -= avg / roll_amount;
    avg += new / roll_amount;
    return avg;

# Convert a (rho, theta) line to (x, y) and draw it on the frame
def draw(img, line, color):
    rho, theta = line
    a = math.cos(theta)
    b = math.sin(theta)
    x0 = a*rho
    y0 = b*rho
    wdtby2 = 1280 / 2
    heiby2 = 720 / 2
    pt1 = (int(x0 + 1500*(-b) + (wdtby2)), int(y0 + 1500*(a) + (heiby2)))
    pt2 = (int(x0 - 1500*(-b) + (wdtby2)), int(y0 - 1500*(a) + (heiby2)))
    cv.line(img, pt1, pt2, color, 3, cv.LINE_AA)

# While dashcam is capturing footage
while vrd.isOpened():
    ret, frame = vrd.read()
    
    # Check for frame capture error
    if not ret:
        break
    
    # Copy image into memory
    in_buffer[:] = frame
    
    start = cv.getTickCount()
    
    # Start streaming the image
    dma.sendchannel.transfer(in_buffer)
    dma.recvchannel.transfer(out_buffer)

    # Signal the VPU to start processing
    vpu.write(0x00,0x81)

    # Wait until results are available
    dma.sendchannel.wait()
    dma.recvchannel.wait()
    
    end = cv.getTickCount()
    total_ticks += (end - start)
    num_frames += 1
    
    # Convert all fixed-point results to floats
    fl_buffer[:] = out_buffer / (1 << (32-10))
    
    # Categorize lines into left and right buckets
    left_lines = []
    right_lines = []
    
    # Sort the Hough lines into two buckets, left and right
    for i in range(0, max_lines):
        rho = fl_buffer[0, i]
        theta = fl_buffer[1, i]
        if theta > deg90_rad + theta_margin:
            left_lines.append((rho, theta))
        elif theta < deg90_rad - theta_margin and theta != 0:
            right_lines.append((rho, theta))

    # Average the left lines
    if left_lines:
        rho, theta = np.average(left_lines, axis=0)
        
        if left_rho_roll == 0:
            left_rho_roll = rho
        else:
            left_rho_roll = roll_avg(left_rho_roll, rho)
        
        if left_theta_roll == 0:
            left_theta_roll = theta
        else:
            left_theta_roll = roll_avg(left_theta_roll, theta)
    
    # Average the right lines
    if right_lines:
        rho, theta = np.average(right_lines, axis=0)
        
        if right_rho_roll == 0:
            right_rho_roll = rho
        else:
            right_rho_roll = roll_avg(right_rho_roll, rho)
        
        if right_theta_roll == 0:
            right_theta_roll = theta
        else:
            right_theta_roll = roll_avg(right_theta_roll, theta)
    
    # We have a result
    if left_theta_roll != 0 and right_theta_roll != 0:
        
        # relative difference in degrees of the left and the center line
        rel_left = left_theta_roll - deg90_rad
        # relative difference in degrees of the right and the center line
        rel_right = deg90_rad - right_theta_roll
        
        color = (255, 0, 0) # blue in BGR
        
        # If the angle of the {left,right} line is double that of the other line
        # that means a departure is detected
        if rel_left > rel_right * angle_sens or rel_right > rel_left * angle_sens:
            # visualize the departure with red lines
            color = (0, 0, 255) # red in BGR
            # and draw some text!
            cv.putText(frame, "Lane Departure Detected!!!", (100, 100), cv.FONT_HERSHEY_DUPLEX, 1.75, color, 1, cv.LINE_AA)
            
        draw(frame, (left_rho_roll, left_theta_roll), color)
        draw(frame, (right_rho_roll, right_theta_roll), color)
        
    vwr.write(frame)
    
# Release resources
vrd.release()
vwr.release()
del in_buffer
del out_buffer
del fl_buffer

# Display the statistics
print("Avg: ", (total_ticks / num_frames) / cv.getTickFrequency(), " s over ", num_frames, " frames")

# Display the resulting video in this notebook
Video(out_file_name, embed=True, width=(max_width/3), height=(max_height/3))

Avg:  0.019302214159722223  s over  720  frames
